In [1]:
import torch
from torch import nn
import torchquad
from torchquad import MonteCarlo
from random import random, randint
from torch.utils.data import DataLoader
from torchvision import datasets
from torchvision.transforms import ToTensor
import itertools

In [2]:
#First we define the boundary of our set of almost desirable gambles.

def make_gam_bnd(a, b, g, l):

    def gam_bnd(x):
        return torch.where(
            x[:, 0] < 0,
            torch.where(
                x[:, 1] < 0,
                -((l * (a * x[:, 0] + b * x[:, 1])) / (g)),
                torch.where(
                    a * l * x[:, 0] + b * g * x[:, 1] < 0,
                    -((a * l * x[:, 0] + b * g * x[:, 1]) / (g)),
                    -((a * l * x[:, 0] + b * g * x[:, 1]) / (l))
                )
            ),
            torch.where(
                x[:, 1] >= 0,
                -((g * (a * x[:, 0] + b * x[:, 1])) / (l)),
                torch.where(
                    a * g * x[:, 0] + b * l * x[:, 1] < 0,
                    -((a * g * x[:, 0] + b * l * x[:, 1]) / (g)),
                    -((a * g * x[:, 0] + b * l * x[:, 1]) / (l))
                )
            )
        )

    return gam_bnd

In [6]:
#Then we define our IP loss function. 
# First we need to declare an integrator, since our IP loss function is an integral functional. 
# Here we use the simple, stochastic Monte Carlo integration method
mc = MonteCarlo()

In [7]:
#Then we define the integrand of our IP loss function in omega_1 (phi_1; the type1/2 penality function for omega_1).

def make_phi(g, l, f):
    def phi(x):
       return torch.where(x[:, 0] < 0, -l * x[:, 0] * 1e-6 * torch.sub(torch.tensor([50]), torch.max(torch.tensor([-50]), torch.min(torch.tensor([50]), f(x))), alpha=1), torch.tensor([0])) + torch.where(x[:, 0] >= 0, g * x[:, 0] * 1e-6 * torch.add(torch.tensor([50]), torch.min(torch.tensor([50]), torch.max(torch.tensor([-50]), f(x))), alpha=1), torch.tensor([0]))
    return phi

In [8]:
#Now use this to define our IP loss function in omega_1.

# Integration domain
domain = torch.Tensor([[-50, 50], [-50, 50]])
# Enable the creation of a computational graph for gradient calculation.
domain.requires_grad = True


def make_ip_loss_1(g, l):

    def ip_loss_1(f):

        penalty = mc.integrate(
            make_phi(g, l, f),
            dim=2,
            N=10000,
            integration_domain=domain,
            backend="torch",
        )

        return penalty

    return ip_loss_1

In [12]:
#Let's test everything to make sure it's working correctly.

gam_bnd_test_1 = make_gam_bnd(1, 1, 1, 2)

test_1a = make_ip_loss_1(1, 2)
test_1b = test_1a(gam_bnd_test_1)
print(test_1b)
# expected result 7.48698

tensor(7.4412, grad_fn=<DivBackward0>)


In [10]:
#Next we define the integrand of our IP loss function in omega_2 (phi_2; type1/2 penality function for omega_2).

def make_psi(g, l, f):
    def psi(x):
       return torch.where(x[:, 1] < 0, -l * x[:, 1] * 1e-6 * torch.sub(torch.tensor([50]), torch.max(torch.tensor([-50]), torch.min(torch.tensor([50]), f(x))), alpha=1), torch.tensor([0])) + torch.where(x[:, 1] >= 0, g * x[:, 1] * 1e-6 * torch.add(torch.tensor([50]), torch.min(torch.tensor([50]), torch.max(torch.tensor([-50]), f(x))), alpha=1), torch.tensor([0]))
    return psi

In [11]:
#Define our IP loss function in omega_2.

def make_ip_loss_2(g, l):

    def ip_loss_2(f):

        penalty = mc.integrate(
            make_psi(g, l, f),
            dim=2,
            N=10000,
            integration_domain=domain,
            backend="torch",
        )

        return penalty

    return ip_loss_2

In [12]:
#Now you create a test to make sure everything is working correctly. 
# Go here to generate test values: https://www.wolframcloud.com/obj/jason.konek/Published/IP-Scoring-Rule-Test.nb

gam_bnd_test_2 = make_gam_bnd(?, ?, ?, ?)

test_2a = 
test_2b = 
print(test_2b)
# expected result ???

tensor(7.5983, grad_fn=<DivBackward0>)


In [13]:
#Finally we define the integrand of our IP loss function in omega_3 (type1/2 penality function for omega_3).

def make_rho(g, l, f):
    def rho(x):
       return 0.5 * l * 1e-6 * torch.square(torch.max(torch.tensor([-50]), torch.min(torch.tensor([0]), f(x)))) + 0.5 * g * 1e-6 * torch.square(torch.min(torch.tensor([50]), torch.max(torch.tensor([0]), f(x))))
    return rho

In [14]:
#Define loss in our IP loss function in omega_3.

def make_ip_loss_3(g, l):

    def ip_loss_3(f):

        penalty = mc.integrate(
            make_rho(g, l, f),
            dim=2,
            N=10000,
            integration_domain=domain,
            backend="torch",
        )

        return penalty

    return ip_loss_3

In [16]:
#Test again

gam_bnd_test_3 = make_gam_bnd(1, 1, 1, 2)

test_3a = make_ip_loss_1(1, 2)
test_3b = test_3a(gam_bnd_test_3)
print(test_3b)
# expected result 7.61728

tensor(7.6300, grad_fn=<DivBackward0>)


In [16]:
class IPLossFunction:

    def __init__(self, g, l):
        # this parameterises our IP loss function
        self.ip_loss_fns = [
            make_ip_loss_1(g, l),
            make_ip_loss_2(g, l),
            make_ip_loss_3(g, l),
        ]
        self.g = g
        self.l = l

    def __call__(self, a, b, target):
        # this is our IP loss function at world omega_(target+1)
        self.a = a**2
        self.b = b**2

        f = make_gam_bnd(self.a, self.b, 1, 2)
        ip_loss_fn = self.ip_loss_fns[target]
        return ip_loss_fn(f)

In [17]:
#Once more, create a test to make sure everything is working correctly. 
# Go here to generate test values: https://www.wolframcloud.com/obj/jason.konek/Published/IP-Scoring-Rule-Test.nb

IP_loss_test = IPLossFunction(?, ?)
a = torch.tensor([?])
b = torch.tensor([?])
c_0 = torch.tensor([0])
c_1 = torch.tensor([1])
c_2 = torch.tensor([2])
test_4a = IP_loss_test(a, b, c_0)
test_4b = IP_loss_test(a, b, c_1)
test_4c = IP_loss_test(a, b, c_2)
print(test_4a, test_4b, test_4c)

#Expected results: ???

tensor(7.4261, grad_fn=<DivBackward0>) tensor(7.4408, grad_fn=<DivBackward0>) tensor(7.4140, grad_fn=<DivBackward0>)


In [109]:
#Now it's time to use our IP loss function to train a neural net classifier. 
# We're going to train it to classify images of clothing items in the Fashion-MNIST dataset.
# For simplicity we restrict attention to 3 cloth items: T-shirt/top (0), Trouser (1), and Pullover (2)

def reduce_dataset(dataset):
    return [
        (datum, i) for datum, i in dataset
        if i < 3
    ]

# Download training data from open datasets.
training_data = datasets.FashionMNIST(
    root="data",
    train=True,
    download=True,
    transform=ToTensor(),
)
training_data = reduce_dataset(training_data)

# Download test data from open datasets.
test_data = datasets.FashionMNIST(
    root="data",
    train=False,
    download=True,
    transform=ToTensor(),
)
test_data = reduce_dataset(test_data)

In [110]:
# Then we set the batchsizes of our training and evaluation datasets and create our data loaders.

batch_size_train = 3
batch_size_eval = 1

train_dataloader = DataLoader(training_data, batch_size=batch_size_train, drop_last=True)
test_dataloader = DataLoader(test_data, batch_size=batch_size_eval, drop_last=True)

In [111]:
# Get cpu or gpu device for training.
device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Using {device} device")

Using cpu device


In [112]:
# Now we define our model. Nothing fancy here. 
# Input layer needs 28 * 28 nodes since the data set is made up of 28×28 pixel grayscale images.
# Hidden layer has 512 nodes
# Output layer only has 2 nodes, because our SDG boundaries have 2 parameters


class NeuralNetwork(nn.Module):
    def __init__(self):
        super(NeuralNetwork, self).__init__()
        self.flatten = nn.Flatten()
        self.linear_relu_stack = nn.Sequential(
            nn.Linear(28 * 28, 512),
            nn.ReLU(),
            nn.Linear(512, 512),
            nn.ReLU(),
            nn.Linear(512, 2)
        )

    def forward(self, x):
        x = self.flatten(x)
        logits = self.linear_relu_stack(x)
        return logits


model = NeuralNetwork().to(device)
print(model)

NeuralNetwork(
  (flatten): Flatten(start_dim=1, end_dim=-1)
  (linear_relu_stack): Sequential(
    (0): Linear(in_features=784, out_features=512, bias=True)
    (1): ReLU()
    (2): Linear(in_features=512, out_features=512, bias=True)
    (3): ReLU()
    (4): Linear(in_features=512, out_features=2, bias=True)
  )
)


In [113]:
#Next we choose the IP loss function that we are going to use to train the neural net.
#We also specify that we are going to update the weights of our model by stochastic gradient descent.

loss_fn = IPLossFunction(?, ?)
optimizer = torch.optim.SGD(model.parameters(), lr=1e-4)

In [114]:
def train(dataloader, model, loss_fn, optimizer):
    size = len(dataloader.dataset)
    model.train()
    for i, (batch, (X, y)) in itertools.product(range(batch_size_train), enumerate(dataloader)):
        # print("batch, (X, y):")
        # print(batch.shape, {X.shape}, {y.shape})
        X, y = X.to(device), y.to(device)

        # Compute prediction error
        pred = model(X)
        z = torch.cat((pred, y.unsqueeze(1)), 1)
        a_i = z[i, 0]
        b_i = z[i, 1]
        target_i = int(z[i, 2])
        loss = loss_fn(a_i, b_i, target_i)

        # Backpropagation
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

In [115]:
def test(dataloader, model, loss_fn):
    size = len(dataloader.dataset)
    num_batches = len(dataloader)
    model.eval()
    test_loss, correct = 0, 0
    with torch.no_grad():
        for i, (X, y) in itertools.product(range(batch_size_eval), dataloader):
            X, y = X.to(device), y.to(device)
            pred = model(X)
            z = torch.cat((pred, y.unsqueeze(1)), 1)
            a_i = z[i, 0]
            b_i = z[i, 1]
            target_i = int(z[i, 2])
            test_loss += loss_fn(a_i, b_i, target_i).item()
            #correct += (pred.argmax(1) == y).type(torch.float).sum().item()
            # print("a_i, b_i, target_i:")
            # print(a_i, b_i, target_i)
    test_loss /= num_batches
    #correct /= size
    print(f"Avg loss: {test_loss:>8f} \n")

In [116]:
epochs = 3
for t in range(epochs):
    print(f"Epoch {t+1}\n-------------------------------")
    train(train_dataloader, model, loss_fn, optimizer)
    test(test_dataloader, model, loss_fn)
print("Done!")

Epoch 1
-------------------------------
Avg loss: 0.717944 

Epoch 2
-------------------------------
Avg loss: 0.608768 

Epoch 3
-------------------------------
Avg loss: 0.561132 

Epoch 4
-------------------------------
Avg loss: 0.533553 

Epoch 5
-------------------------------
Avg loss: 0.514564 

Done!


In [123]:
#Now it's time to look at what predictions our neural net is making. 
# Let this run and then look at the outputs on the last two samples.
# What were the two samples: T-shirt/top, Trouser, or Pullover?
# Which parameters did the neural net predict? Remember to square the parameter values to get the predicted model!
# Good? Bad?

def train_model_output(dataloader, model, loss_fn, optimizer):
    size = len(dataloader.dataset)
    model.train()
    for i, (batch, (X, y)) in itertools.product(range(1), enumerate(dataloader)):
        X, y = X.to(device), y.to(device)

        # Compute prediction error
        pred = model(X)
        z = torch.cat((pred, y.unsqueeze(1)), 1)
        a_i = z[i, 0]
        b_i = z[i, 1]
        target_i = int(z[i, 2])
        print("a_i, b_i, target_i:")
        print(a_i, b_i, target_i)
        loss = loss_fn(a_i, b_i, target_i)

        # Backpropagation
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

epochs = 1
for t in range(epochs):
    print(f"Epoch {t+1}\n-------------------------------")
    train_model_output(train_dataloader, model, loss_fn, optimizer)
print("Done!")

Epoch 1
-------------------------------
a_i, b_i, target_i:
tensor(8.4382, grad_fn=<SelectBackward0>) tensor(0.9280, grad_fn=<SelectBackward0>) 0
a_i, b_i, target_i:
tensor(-0.0190, grad_fn=<SelectBackward0>) tensor(-0.1030, grad_fn=<SelectBackward0>) 2
a_i, b_i, target_i:
tensor(0.3143, grad_fn=<SelectBackward0>) tensor(-5.5507, grad_fn=<SelectBackward0>) 1
a_i, b_i, target_i:
tensor(6.5010, grad_fn=<SelectBackward0>) tensor(0.3920, grad_fn=<SelectBackward0>) 0
a_i, b_i, target_i:
tensor(0.3125, grad_fn=<SelectBackward0>) tensor(0.1688, grad_fn=<SelectBackward0>) 2
a_i, b_i, target_i:
tensor(7.9703, grad_fn=<SelectBackward0>) tensor(0.6189, grad_fn=<SelectBackward0>) 0
a_i, b_i, target_i:
tensor(2.3033, grad_fn=<SelectBackward0>) tensor(0.1585, grad_fn=<SelectBackward0>) 0
a_i, b_i, target_i:
tensor(8.2818, grad_fn=<SelectBackward0>) tensor(0.3731, grad_fn=<SelectBackward0>) 0
a_i, b_i, target_i:
tensor(-0.2300, grad_fn=<SelectBackward0>) tensor(-6.7647, grad_fn=<SelectBackward0>) 1
a